In [4]:
import pandas as pd
import streamlit as st
from streamlit_folium import folium_static
import folium
import requests

In [16]:
recent_tnx = pd.read_csv('data/recent_tnx.csv')
recent_tnx.head()

month        town flat_type block        street_name storey_range  \
0  2023-01  ANG MO KIO    2 ROOM   406  ANG MO KIO AVE 10     01 TO 03   
1  2023-01  ANG MO KIO    2 ROOM   323   ANG MO KIO AVE 3     04 TO 06   
2  2023-01  ANG MO KIO    2 ROOM   314   ANG MO KIO AVE 3     04 TO 06   
3  2023-01  ANG MO KIO    2 ROOM   314   ANG MO KIO AVE 3     07 TO 09   
4  2023-01  ANG MO KIO    2 ROOM   170   ANG MO KIO AVE 4     01 TO 03   

   floor_area_sqm flat_model  lease_commence_date  resale_price  \
0            44.0   Improved                 1979      267000.0   
1            49.0   Improved                 1977      300000.0   
2            44.0   Improved                 1978      280000.0   
3            44.0   Improved                 1978      282000.0   
4            45.0   Improved                 1986      289800.0   

   remaining_lease_yr                address  Latitude   Longitude  
0                  55  406 ANG MO KIO AVE 10  1.362005  103.853880  
1                  53   323 ANG MO KIO AVE 3  1.367908  103.847714  
2                  54   314 ANG MO KIO AVE 3  1.366227  103.850086  
3                  54   314 ANG MO KIO AVE 3  1.366227  103.850086  
4                  62   170 ANG MO KIO AVE 4  1.374001  103.836432

In [17]:
recent_tnx = recent_tnx[["Latitude", "Longitude", "flat_type", "storey_range", "remaining_lease_yr", "resale_price"]]
recent_tnx.head()

Latitude   Longitude flat_type storey_range  remaining_lease_yr  \
0  1.362005  103.853880    2 ROOM     01 TO 03                  55   
1  1.367908  103.847714    2 ROOM     04 TO 06                  53   
2  1.366227  103.850086    2 ROOM     04 TO 06                  54   
3  1.366227  103.850086    2 ROOM     07 TO 09                  54   
4  1.374001  103.836432    2 ROOM     01 TO 03                  62   

   resale_price  
0      267000.0  
1      300000.0  
2      280000.0  
3      282000.0  
4      289800.0

In [13]:
address = "725 Clementi West Street 2"
pred_price = "600,000"

def getcoordinates(address):
    req = requests.get('https://developers.onemap.sg/commonapi/search?searchVal='+address+'&returnGeom=Y&getAddrDetails=Y&pageNum=1')
    resultsdict = eval(req.text)
    if len(resultsdict['results'])>0:
        return resultsdict['results'][0]['LATITUDE'], resultsdict['results'][0]['LONGITUDE']
    else:
        pass
    
address_lat = getcoordinates(address)[0]
address_long = getcoordinates(address)[1]

In [24]:
map = folium.Map(location=[address_lat, address_long], zoom_start=17, control_scale=True)

for index, location_info in recent_tnx.iterrows():
    folium.CircleMarker(location=[location_info["Latitude"],location_info["Longitude"]],
                         radius=5,
                         color="crimson", 
                         fill=True,
                         fill_color="crimson",
                         popup=location_info[["flat_type", "storey_range", "remaining_lease_yr", "resale_price"]]).add_to(map)
    
folium.Marker(location=[address_lat, address_long], popup= [address, pred_price]).add_to(map)
map

## If there are overlapping transactions only one of it will show, unless there's a way to add some difference to the long lat
